In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from boardgame2 import ReversiEnv
from dynamic_programming import generate_uniform_stochastic_policy, policy_evaluation, stochastic_policy_eval_step, generate_deterministic_policy, deterministic_policy_eval_step
from tree_search import bfs_cannonical
import numpy as np

# Programación dinámica

En esta parte no es necesario la implementación de código ya que ya esta todo resuelto. Si tiene que responder algunas preguntas en **EDX**.

Si lo desea puede ver el código para analizar la implementación, pero es opcional

Si quiere profundizar le recomendamos mirar:

- bfs_cannonical cannonical de la librería tree_search
- policy_evaluation, policy_improve, policy_iterartion y value_iteration de dynamic_programming

### La idea de esta sección es generar las $V^*(s)$y $\Pi^*(s)$ (óptimas) en 4x4 para poder hacer los análisis posteriores
### Por eso se deben correr todas las celdas

# Busqueda de todos los estados canónicos

Solo desde el punto de vista del jugador +1

In [35]:
%%time
board_size = 4
states = bfs_cannonical(board_size, verbose=1)

CPU times: user 1min 19s, sys: 12.6 s, total: 1min 32s
Wall time: 1min 15s


Al ser canónico, no es necesario que el jugador sea parte del estado ya que siempre se puede pensar como que le toca jugar al jugador +1

In [36]:
# Listamos los primeros 5 estados encontrados
for s in list(states.keys())[0:20]:
    print(s)

(0, 0, 0, 0, 0, 1, -1, 0, 0, -1, 1, 0, 0, 0, 0, 0)
(0, 0, -1, 0, 0, -1, -1, 0, 0, 1, -1, 0, 0, 0, 0, 0)
(0, 0, 0, 0, 0, -1, -1, -1, 0, 1, -1, 0, 0, 0, 0, 0)
(0, 0, 0, 0, 0, -1, 1, 0, -1, -1, -1, 0, 0, 0, 0, 0)
(0, 0, 0, 0, 0, -1, 1, 0, 0, -1, -1, 0, 0, -1, 0, 0)
(0, -1, 1, 0, 0, -1, 1, 0, 0, -1, 1, 0, 0, 0, 0, 0)
(0, 0, 1, -1, 0, 1, -1, 0, 0, -1, 1, 0, 0, 0, 0, 0)
(0, 0, 1, 0, 0, 1, 1, 0, 0, -1, -1, -1, 0, 0, 0, 0)
(0, -1, 0, 0, 0, -1, 1, 1, 0, -1, 1, 0, 0, 0, 0, 0)
(0, 0, 0, -1, 0, 1, -1, 1, 0, -1, 1, 0, 0, 0, 0, 0)
(0, 0, 0, 0, 0, 1, 1, 1, 0, -1, -1, -1, 0, 0, 0, 0)
(0, 0, 0, 0, -1, -1, -1, 0, 1, 1, 1, 0, 0, 0, 0, 0)
(0, 0, 0, 0, 0, 1, -1, 0, 1, -1, 1, 0, -1, 0, 0, 0)
(0, 0, 0, 0, 0, 1, -1, 0, 1, 1, -1, 0, 0, 0, -1, 0)
(0, 0, 0, 0, -1, -1, -1, 0, 0, 1, 1, 0, 0, 1, 0, 0)
(0, 0, 0, 0, 0, 1, -1, 0, 0, -1, 1, 0, -1, 1, 0, 0)
(0, 0, 0, 0, 0, 1, -1, 0, 0, 1, -1, 0, 0, 1, -1, 0)
(-1, -1, -1, 0, 0, -1, -1, 0, 0, 1, -1, 0, 0, 0, 0, 0)
(0, 1, -1, 0, -1, -1, -1, 0, 0, 1, -1, 0, 0, 0, 0, 0)
(0, 

In [37]:
# Guardamos el estado s0
s0 = list(states.keys())[0]

In [38]:
s0

(0, 0, 0, 0, 0, 1, -1, 0, 0, -1, 1, 0, 0, 0, 0, 0)

In [39]:
# Mostrado como tablero
np.array(s0).reshape(4,4)

array([[ 0,  0,  0,  0],
       [ 0,  1, -1,  0],
       [ 0, -1,  1,  0],
       [ 0,  0,  0,  0]], dtype=int8)

Cada estado se guarda con todas sus posibles acciones y dado el estado y la acción, se guarda:
- **next_node**: el próximo estado al ejecutar esa acción
- **done**: si termina el juego (episodio)
- **winner**: si al ejecutar la acción alguno de los dos jugadores gana: (+1 o -1)

In [40]:
for action, next_data in states[s0].items():
    print(f'acción: {action}')
    print(next_data)

acción: (0, 2)
{'done': False, 'winner': -0.0, 'next_node': (0, 0, -1, 0, 0, -1, -1, 0, 0, 1, -1, 0, 0, 0, 0, 0)}
acción: (1, 3)
{'done': False, 'winner': -0.0, 'next_node': (0, 0, 0, 0, 0, -1, -1, -1, 0, 1, -1, 0, 0, 0, 0, 0)}
acción: (2, 0)
{'done': False, 'winner': -0.0, 'next_node': (0, 0, 0, 0, 0, -1, 1, 0, -1, -1, -1, 0, 0, 0, 0, 0)}
acción: (3, 1)
{'done': False, 'winner': -0.0, 'next_node': (0, 0, 0, 0, 0, -1, 1, 0, 0, -1, -1, 0, 0, -1, 0, 0)}


# Ejemplo de un estado terminal

In [41]:
done = 0
for s in states.keys():
    print(s)
    for action, next_data in states[s].items():
        if next_data['done']:
            print(s)
            print(f'acción: {action}')
            print(next_data)
            done = done + 1
            print()
            break
    """if done > 5:
        break """

(0, 0, 0, 0, 0, 1, -1, 0, 0, -1, 1, 0, 0, 0, 0, 0)
(0, 0, -1, 0, 0, -1, -1, 0, 0, 1, -1, 0, 0, 0, 0, 0)
(0, 0, 0, 0, 0, -1, -1, -1, 0, 1, -1, 0, 0, 0, 0, 0)
(0, 0, 0, 0, 0, -1, 1, 0, -1, -1, -1, 0, 0, 0, 0, 0)
(0, 0, 0, 0, 0, -1, 1, 0, 0, -1, -1, 0, 0, -1, 0, 0)
(0, -1, 1, 0, 0, -1, 1, 0, 0, -1, 1, 0, 0, 0, 0, 0)
(0, 0, 1, -1, 0, 1, -1, 0, 0, -1, 1, 0, 0, 0, 0, 0)
(0, 0, 1, 0, 0, 1, 1, 0, 0, -1, -1, -1, 0, 0, 0, 0)
(0, -1, 0, 0, 0, -1, 1, 1, 0, -1, 1, 0, 0, 0, 0, 0)
(0, 0, 0, -1, 0, 1, -1, 1, 0, -1, 1, 0, 0, 0, 0, 0)
(0, 0, 0, 0, 0, 1, 1, 1, 0, -1, -1, -1, 0, 0, 0, 0)
(0, 0, 0, 0, -1, -1, -1, 0, 1, 1, 1, 0, 0, 0, 0, 0)
(0, 0, 0, 0, 0, 1, -1, 0, 1, -1, 1, 0, -1, 0, 0, 0)
(0, 0, 0, 0, 0, 1, -1, 0, 1, 1, -1, 0, 0, 0, -1, 0)
(0, 0, 0, 0, -1, -1, -1, 0, 0, 1, 1, 0, 0, 1, 0, 0)
(0, 0, 0, 0, 0, 1, -1, 0, 0, -1, 1, 0, -1, 1, 0, 0)
(0, 0, 0, 0, 0, 1, -1, 0, 0, 1, -1, 0, 0, 1, -1, 0)
(-1, -1, -1, 0, 0, -1, -1, 0, 0, 1, -1, 0, 0, 0, 0, 0)
(0, 1, -1, 0, -1, -1, -1, 0, 0, 1, -1, 0, 0, 0, 0, 0)
(0, 

(-1, -1, -1, 1, -1, -1, 1, 1, 0, 1, 1, 1, 0, 0, 0, 0)
(-1, -1, -1, 1, -1, -1, 1, 1, 0, 1, 1, 1, 0, 0, 0, 0)
acción: (-1, 0)
{'done': True, 'winner': 1, 'next_node': (1, 1, 1, -1, 1, 1, -1, -1, 0, -1, -1, -1, 0, 0, 0, 0)}

(0, 1, -1, 1, -1, -1, 1, 1, 0, -1, 1, 1, 0, -1, 0, 0)
(0, 1, -1, 1, -1, -1, -1, 1, 0, -1, -1, 1, 0, 0, -1, 0)
(0, 1, -1, 1, -1, -1, 1, 1, 0, 1, -1, 1, 0, 0, 0, -1)
(0, 1, -1, 1, -1, -1, -1, 1, -1, -1, -1, 1, 0, 0, 0, 0)
(0, 1, -1, 1, -1, -1, -1, -1, -1, 1, -1, 0, 1, 0, 0, 0)
(0, 1, 0, 1, -1, -1, 1, -1, -1, -1, -1, 0, 1, -1, 0, 0)
(0, 1, 0, 1, -1, -1, 1, -1, -1, -1, -1, 0, 1, 0, -1, 0)
(-1, 1, 0, 1, -1, -1, 1, -1, -1, 1, -1, 0, 0, 1, 0, 0)
(0, 1, -1, 1, -1, -1, -1, -1, -1, 1, -1, 0, 0, 1, 0, 0)
(0, 1, 0, 1, -1, 1, 1, -1, -1, -1, -1, 0, 0, 1, -1, 0)
(0, 1, 0, 1, -1, -1, 1, -1, -1, -1, -1, -1, 0, 0, 1, 0)
(0, 1, 0, 1, -1, -1, 1, -1, -1, -1, -1, 0, 0, -1, 1, 0)
(0, 1, 0, 1, -1, -1, 1, -1, -1, -1, -1, 0, 0, 0, 1, -1)
(0, 1, -1, 1, -1, -1, -1, 1, 0, -1, -1, 1, 0, -1, 0, 0)


(0, -1, -1, -1, 1, 1, 1, -1, 1, 1, 1, 0, 0, -1, 1, 0)
(0, -1, 1, 0, 1, 1, -1, -1, 1, 1, 1, -1, 0, -1, 1, 0)
(0, -1, 1, 0, 1, 1, 1, -1, 1, 1, 1, 0, 0, -1, -1, -1)
(0, -1, 1, 0, 1, 1, 1, -1, 1, 1, 1, 0, 0, -1, -1, -1)
acción: (0, 0)
{'done': True, 'winner': -1, 'next_node': (-1, -1, -1, 0, -1, -1, -1, 1, -1, -1, -1, 0, 0, 1, 1, 1)}

(0, -1, -1, -1, 1, 1, -1, -1, 1, -1, 1, 0, 0, -1, 0, 1)
(0, -1, 1, 0, 1, 1, -1, -1, 1, -1, -1, -1, 0, -1, 0, 1)
(1, 1, 1, 0, 1, 1, -1, 0, 1, -1, -1, -1, 0, -1, 0, 0)
(-1, -1, 1, 0, 1, -1, 1, 1, 1, -1, -1, -1, 0, -1, 0, 0)
(0, -1, -1, -1, 1, 1, -1, 0, 1, -1, 1, -1, 0, -1, 0, 1)
(0, -1, 1, 0, 1, 1, -1, 0, 1, -1, -1, -1, 0, -1, -1, 1)
(1, -1, -1, -1, 0, 1, 1, -1, 1, 1, -1, 0, 1, -1, 0, 0)
(1, -1, -1, -1, 0, 1, -1, 0, 1, 1, 1, -1, 1, -1, 0, 0)
(1, -1, -1, -1, 0, 1, -1, 0, 1, 1, -1, 0, 1, -1, -1, 0)
(0, -1, -1, -1, 1, 1, -1, 0, 1, 1, 1, -1, 1, -1, 0, 0)
(0, -1, -1, -1, 1, 1, -1, 0, 1, 1, -1, 0, 1, -1, -1, 0)
(0, -1, -1, -1, 0, -1, -1, -1, 1, 1, 1, 0, 1, 1, 1, 0)
(

(0, 0, 0, -1, -1, -1, -1, -1, 1, 1, -1, -1, 0, 1, -1, -1)
(0, 0, 0, -1, -1, -1, -1, 1, 0, -1, 1, 1, 0, 1, 1, 1)
(0, 1, -1, -1, 0, 1, -1, 1, 0, -1, -1, 1, -1, -1, -1, 0)
(0, 1, 0, -1, 0, 1, 1, -1, 0, -1, 1, -1, -1, -1, -1, -1)
(-1, 0, 1, -1, 0, -1, 1, -1, 0, 1, -1, -1, 0, 1, -1, -1)
(0, 0, 1, -1, -1, -1, -1, -1, 0, -1, 1, -1, 0, 1, -1, -1)
(0, 0, 1, -1, 0, 1, 1, -1, -1, -1, -1, -1, 0, 1, -1, -1)
(0, 0, 1, -1, 0, 1, -1, -1, 0, -1, 1, -1, -1, -1, -1, -1)
(1, 0, 0, -1, -1, 1, -1, -1, 0, 1, 1, -1, 0, 1, 1, 1)
(1, 0, 0, -1, -1, 1, -1, 1, 0, -1, 1, 0, -1, 1, 1, 1)
(0, 1, 0, -1, -1, 1, -1, -1, 0, 1, 1, -1, 0, 1, 1, 1)
(0, 1, 0, -1, -1, 1, -1, 1, 0, -1, 1, 0, -1, 1, 1, 1)
(0, -1, -1, -1, -1, -1, 1, 1, 0, 1, 1, 0, 0, 1, 1, 1)
(0, 0, 1, -1, -1, -1, 1, -1, 0, 1, 1, -1, 0, 1, 1, 1)
(0, 0, 1, -1, -1, -1, -1, 1, 0, -1, 1, 0, -1, 1, 1, 1)
(0, 0, 0, -1, 1, 1, -1, -1, 0, 1, 1, -1, -1, 1, 1, 1)
(-1, -1, -1, 1, 0, -1, 1, 1, -1, -1, -1, -1, 1, 0, 0, 0)
(-1, -1, -1, 1, 0, -1, 1, 1, 0, -1, -1, -1, 1, -1, 0, 

(1, 0, 0, 0, 1, 1, -1, -1, 1, -1, -1, 0, -1, -1, -1, 1)
(1, 0, 0, 0, 1, 1, -1, 0, 1, -1, -1, -1, -1, -1, -1, 1)
(1, 1, 1, -1, -1, -1, -1, 0, 0, -1, 1, 0, 0, 1, 1, 1)
(1, 1, 1, 0, -1, -1, -1, -1, 0, -1, 1, 0, 0, 1, 1, 1)
(1, 1, 1, 0, -1, -1, 1, 0, 0, -1, -1, -1, 0, 1, 1, 1)
(1, -1, 0, 0, 1, -1, -1, 0, 1, -1, 1, 0, -1, 1, 1, 1)
(1, -1, 1, 0, -1, -1, -1, 0, 0, -1, 1, -1, 0, 1, 1, 1)
(1, 0, 1, -1, -1, 1, -1, 0, 0, -1, 1, -1, 0, 1, 1, 1)
(1, 0, 1, 0, -1, -1, -1, -1, 0, -1, 1, -1, 0, 1, 1, 1)
(1, 1, 1, 0, -1, 1, -1, -1, 0, -1, -1, -1, -1, 1, 0, 0)
(0, 1, 1, 0, -1, 1, -1, -1, 1, -1, -1, 0, -1, -1, -1, 0)
(0, 1, 1, 0, -1, -1, 1, -1, 0, -1, 1, 1, -1, -1, -1, 0)
(0, 1, 1, 0, -1, -1, 1, -1, 0, -1, -1, -1, -1, 1, 0, -1)
(0, 1, 1, 0, -1, 1, 1, 1, 0, -1, 1, -1, -1, -1, -1, 0)
(0, 1, 1, 0, -1, -1, -1, -1, 0, -1, 1, -1, -1, 1, 1, 0)
(0, 1, 1, 0, -1, 1, 1, 0, 0, -1, 1, -1, -1, -1, -1, -1)
(0, 1, 1, 0, -1, -1, -1, -1, 0, -1, 1, -1, -1, 1, 0, 1)
(0, 1, 1, 0, -1, 1, 1, 0, 0, -1, 1, -1, -1, -1, -1, 1)
(0, 

...

(-1, -1, 1, 1, -1, -1, -1, 0, -1, -1, -1, -1, -1, 1, 1, 1)
acción: (1, 3)
{'done': True, 'winner': 0, 'next_node': (1, 1, -1, -1, 1, 1, 1, -1, 1, 1, -1, -1, 1, -1, -1, -1)}

(-1, 0, 1, 1, -1, -1, -1, 1, -1, -1, 1, 1, -1, 1, 1, 1)
(-1, 0, 1, 1, -1, -1, -1, 1, -1, -1, 1, 1, -1, 1, 1, 1)
acción: (0, 1)
{'done': True, 'winner': -1, 'next_node': (1, -1, -1, -1, 1, -1, -1, -1, 1, -1, -1, -1, 1, -1, -1, -1)}

(-1, 0, 1, 1, -1, -1, 1, 1, 1, 1, 1, 1, 1, -1, -1, 1)
(-1, 0, 1, 1, -1, -1, 1, 1, 1, 1, 1, 1, 1, -1, -1, 1)
acción: (0, 1)
{'done': True, 'winner': -1, 'next_node': (1, -1, -1, -1, 1, -1, -1, -1, -1, -1, -1, -1, -1, 1, 1, -1)}

(-1, -1, 1, 1, -1, 1, -1, 0, 1, 1, -1, -1, 1, 1, 1, 1)
(-1, -1, 1, 1, -1, 1, -1, 0, 1, 1, -1, -1, 1, 1, 1, 1)
acción: (1, 3)
{'done': True, 'winner': -1, 'next_node': (1, 1, -1, -1, 1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1)}

(-1, 0, 1, 1, -1, -1, -1, -1, 1, 1, -1, -1, 1, 1, 1, 1)
(-1, 0, 1, 1, -1, -1, -1, -1, 1, 1, -1, -1, 1, 1, 1, 1)
acción: (0, 1)
{'done':


(-1, 1, 1, 0, -1, -1, 1, 1, -1, -1, -1, -1, 1, 1, -1, -1)
(-1, 1, 1, 0, -1, -1, 1, 1, -1, -1, -1, -1, 1, 1, -1, -1)
acción: (-1, 0)
{'done': True, 'winner': 1, 'next_node': (1, -1, -1, 0, 1, 1, -1, -1, 1, 1, 1, 1, -1, -1, 1, 1)}

(-1, 1, 1, 0, -1, -1, -1, -1, -1, -1, 1, -1, 1, 1, -1, -1)
(-1, 1, 1, 0, -1, -1, -1, -1, -1, -1, 1, -1, 1, 1, -1, -1)
acción: (0, 3)
{'done': True, 'winner': 0, 'next_node': (1, -1, -1, -1, 1, 1, -1, 1, 1, -1, -1, 1, -1, -1, 1, 1)}

(1, 1, 1, 1, 1, -1, 1, -1, 1, 1, -1, 0, 1, 1, 0, -1)
(1, 1, 1, 1, 1, -1, 1, -1, 1, 1, -1, 0, 1, 1, 0, -1)
acción: (2, 3)
{'done': True, 'winner': -1, 'next_node': (-1, -1, -1, -1, -1, 1, -1, -1, -1, -1, -1, -1, -1, -1, 0, 1)}

(1, 1, 1, 0, 1, -1, 1, -1, 1, 1, 1, 1, 1, 1, 0, -1)
(1, 1, 1, 0, 1, -1, 1, -1, 1, 1, 1, 1, 1, 1, 0, -1)
acción: (0, 3)
{'done': True, 'winner': -1, 'next_node': (-1, -1, -1, -1, -1, 1, -1, -1, -1, -1, -1, -1, -1, -1, 0, 1)}

(1, 1, 1, 0, 1, 1, -1, -1, 1, -1, -1, -1, 1, 1, 1, -1)
(1, 1, 1, 0, 1, 1, -1, -1, 1,


(1, -1, -1, 1, 1, 1, -1, 1, -1, -1, -1, -1, 0, 1, 1, 1)
(1, -1, -1, 1, 1, 1, -1, 1, -1, -1, -1, -1, 0, 1, 1, 1)
acción: (3, 0)
{'done': True, 'winner': -1, 'next_node': (-1, 1, 1, -1, -1, -1, -1, -1, -1, -1, 1, 1, -1, -1, -1, -1)}

(1, -1, -1, 1, 0, -1, -1, 1, -1, -1, -1, -1, 1, 1, 1, 1)
(1, -1, -1, 1, 0, -1, -1, 1, -1, -1, -1, -1, 1, 1, 1, 1)
acción: (1, 0)
{'done': True, 'winner': -1, 'next_node': (-1, 1, 1, -1, -1, -1, -1, -1, -1, -1, 1, 1, -1, -1, -1, -1)}

(1, 1, 1, 1, -1, 1, -1, 1, -1, -1, 1, 0, -1, 1, 1, 1)
(1, 1, 1, 1, -1, 1, -1, 1, -1, -1, 1, 0, -1, 1, 1, 1)
acción: (2, 3)
{'done': True, 'winner': -1, 'next_node': (-1, -1, -1, -1, 1, -1, -1, -1, 1, 1, -1, -1, 1, -1, -1, -1)}

(1, 0, -1, 1, 1, -1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1)
(1, 0, -1, 1, 1, -1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1)
acción: (0, 1)
{'done': True, 'winner': -1, 'next_node': (-1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, 0, -1, -1, -1, -1)}

(1, 1, 1, 1, -1, -1, -1, 1, -1, -1, -1, -1, 0, 1, 1, 1)
(1, 1, 1, 1, -1, -1, -1,


(1, 0, -1, -1, 1, 1, -1, 1, 1, -1, 1, 1, -1, 1, 1, 1)
(1, 0, -1, -1, 1, 1, -1, 1, 1, -1, 1, 1, -1, 1, 1, 1)
acción: (0, 1)
{'done': True, 'winner': -1, 'next_node': (-1, -1, 1, 1, -1, -1, -1, -1, -1, 1, -1, -1, 1, -1, -1, -1)}

(1, 1, -1, -1, 1, 1, -1, 0, -1, 1, 1, 1, -1, 1, 1, 1)
(1, 1, -1, -1, 1, 1, -1, 0, -1, 1, 1, 1, -1, 1, 1, 1)
acción: (1, 3)
{'done': True, 'winner': -1, 'next_node': (-1, -1, 1, 1, -1, -1, -1, -1, 1, -1, -1, -1, 1, -1, -1, -1)}

(1, 1, -1, -1, 1, 1, 1, 1, -1, -1, 1, 1, -1, 0, -1, 1)
(1, 1, -1, -1, 1, 1, 1, 1, -1, -1, 1, 1, -1, 0, -1, 1)
acción: (3, 1)
{'done': True, 'winner': -1, 'next_node': (-1, -1, 1, 1, -1, -1, -1, -1, 1, -1, -1, -1, 1, -1, -1, -1)}

(1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, -1, 1, -1, 0)
(1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, -1, 1, -1, 0)
acción: (3, 3)
{'done': True, 'winner': -1, 'next_node': (-1, -1, -1, -1, -1, -1, -1, -1, 0, -1, -1, -1, 1, -1, -1, -1)}

(1, 1, 1, 1, 1, 1, 1, 1, 0, -1, 1, 1, -1, 0, -1, 1)
(1, 1, 1, 1, 1, 1, 1, 1, 0, -1, 1, 1,

{'done': True, 'winner': -1, 'next_node': (-1, -1, -1, 1, -1, -1, -1, 1, -1, 1, -1, 1, -1, 1, 1, 1)}

(-1, 0, -1, -1, 1, -1, -1, -1, 1, -1, -1, -1, 1, 1, 1, -1)
(-1, 0, -1, -1, 1, -1, -1, -1, 1, -1, -1, -1, 1, 1, 1, -1)
acción: (0, 1)
{'done': True, 'winner': 0, 'next_node': (1, -1, 1, 1, -1, -1, 1, 1, -1, -1, 1, 1, -1, -1, -1, 1)}

(-1, -1, -1, -1, -1, -1, 1, -1, -1, -1, -1, 0, -1, -1, -1, -1)
(-1, -1, -1, -1, -1, -1, 1, -1, -1, -1, -1, 0, -1, -1, -1, -1)
acción: (-1, 0)
{'done': True, 'winner': 1, 'next_node': (1, 1, 1, 1, 1, 1, -1, 1, 1, 1, 1, 0, 1, 1, 1, 1)}

(-1, 0, -1, -1, -1, -1, -1, 1, -1, -1, -1, 1, -1, -1, -1, -1)
(-1, 0, -1, -1, -1, -1, -1, 1, -1, -1, -1, 1, -1, -1, -1, -1)
acción: (0, 1)
{'done': True, 'winner': 1, 'next_node': (1, -1, 1, 1, 1, 1, -1, -1, 1, 1, 1, -1, 1, 1, 1, 1)}

(1, 1, 1, 1, 1, 1, 1, 1, -1, 1, -1, 1, 0, -1, 1, 1)
(1, 1, 1, 1, 1, 1, 1, 1, -1, 1, -1, 1, 0, -1, 1, 1)
acción: (3, 0)
{'done': True, 'winner': -1, 'next_node': (-1, -1, -1, -1, -1, -1, -1, -1, -

La acción (-1, 0) es la acción PASS. En principio solo se ejecuta si no hay opciones válidas

In [42]:
states[(1, 1, 1, -1, 0, 1, 1, 0, 0, -1, 1, 1, 0, 0, 0, 0)]

{(2, 0): {'done': False,
  'winner': -0.0,
  'next_node': (-1, -1, -1, 1, 0, -1, -1, 0, -1, -1, -1, -1, 0, 0, 0, 0)},
 (3, 0): {'done': True,
  'winner': -1,
  'next_node': (-1, -1, -1, 1, 0, -1, -1, 0, 0, -1, -1, -1, -1, 0, 0, 0)},
 (3, 1): {'done': False,
  'winner': -0.0,
  'next_node': (-1, -1, -1, 1, 0, -1, -1, 0, 0, -1, -1, -1, 0, -1, 0, 0)}}

# Policy Evaluation

### Politica estocástica

In [43]:
stochastic_pi = generate_uniform_stochastic_policy(states)

In [44]:
# ejemplos
stochastic_pi[(0, 0, -1, 0, 0, -1, -1, 0, 0, 1, -1, 0, 0, 0, 0, 0)]

{(0, 1): 0.3333333333333333,
 (0, 3): 0.3333333333333333,
 (2, 3): 0.3333333333333333}

In [45]:
stochastic_pi[(0, 0, -1, 0, 0, -1, -1, 0, 0, 1, -1, 0, 0, 0, 0, 0)]

{(0, 1): 0.3333333333333333,
 (0, 3): 0.3333333333333333,
 (2, 3): 0.3333333333333333}

Esto genera una política con distribución uniforme que luego será evaluada usuando **policy evaluation**

In [46]:
V_stochastic, iters = policy_evaluation(stochastic_policy_eval_step, 
                             states, 
                             stochastic_pi, 1e-8, verbose=1)

Iteration number:  1 2 3 4 5 6 7 8 9 10 11 12 13 


#### Ejemplos de la V luego de converger

In [47]:
V_stochastic[(0, 0, 0, 0, 0, 1, -1, 0, 0, -1, 1, 0, 0, 0, 0, 0)]

-0.2403001935859148

In [48]:
V_stochastic[(0, 0, -1, 0, 0, -1, -1, 0, 0, 1, -1, 0, 0, 0, 0, 0)]

0.2403001935859148

### Política determinística

In [49]:
det_pi = generate_deterministic_policy(states)

In [50]:
det_pi[(0, 0, 0, 0, 0, 1, -1, 0, 0, -1, 1, 0, 0, 0, 0, 0)]

(3, 1)

In [51]:
det_pi[(0, 0, -1, 0, 0, -1, -1, 0, 0, 1, -1, 0, 0, 0, 0, 0)]

(0, 1)

Notar que ahora la política dado el estado tiene solo una acción posible que se construyó de manera arbitraria

In [52]:
# Run it multiple times to check it takes different number of iterations to converge
V_det, _ = policy_evaluation(deterministic_policy_eval_step, 
                             states, 
                             det_pi, 1e-8, verbose=1)

Iteration number:  1 2 3 4 5 6 7 8 9 10 11 12 13 


#### Ejemplos de la V luego de converger

In [53]:
V_det[(0, 0, -1, 0, 0, -1, -1, 0, 0, 1, -1, 0, 0, 0, 0, 0)]

1

In [54]:
det_pi[(0, 0, -1, 0, 0, -1, -1, 0, 0, 1, -1, 0, 0, 0, 0, 0)]

(0, 1)

In [55]:
V_det[(0, 0, -1, 0, 0, -1, -1, 0, 0, 1, -1, 0, 0, 0, 0, 0)]

1

# Policy Iteration

Partiendo de cualquier política (estocástica o determinística), por medio de Policy Iteration se puede obtener las óptimas 

In [56]:
from dynamic_programming import policy_improve, policy_iteration, generate_deterministic_policy

In [57]:
%%time
initial_policy = generate_deterministic_policy(states)
optimum_policy, optimum_V = policy_iteration(states, initial_policy, verbose = 1)

Iteration number:  1 2 3 4 5 6 7 8 9 10 11 12 
Number of differences of new policy vs old policy: 12492
---------------------------
Iteration number:  1 2 3 4 5 6 7 8 9 10 11 12 
Number of differences of new policy vs old policy: 1981
---------------------------
Iteration number:  1 2 3 4 5 6 7 8 9 10 11 12 
Number of differences of new policy vs old policy: 531
---------------------------
Iteration number:  1 2 3 4 5 6 7 8 9 10 11 12 13 
Number of differences of new policy vs old policy: 123
---------------------------
Iteration number:  1 2 3 4 5 6 7 8 9 10 11 12 13 
Number of differences of new policy vs old policy: 33
---------------------------
Iteration number:  1 2 3 4 5 6 7 8 9 10 11 12 13 
Number of differences of new policy vs old policy: 8
---------------------------
Iteration number:  1 2 3 4 5 6 7 8 9 10 11 12 13 
Number of differences of new policy vs old policy: 2
---------------------------
Iteration number:  1 2 3 4 5 6 7 8 9 10 11 12 13 
Number of differences of new p

In [58]:
np.save('pi_mdp', optimum_policy)
np.save('v_mdp', optimum_V)

In [59]:
optimum_policy[(0, 0, -1, 0, 0, -1, -1, 0, 0, 1, -1, 0, 0, 0, 0, 0)]

(0, 3)

In [60]:
np.array((0, 0, -1, 0, 0, -1, -1, 0, 0, 1, -1, 0, 0, 0, 0, 0)).reshape(4,4)

array([[ 0,  0, -1,  0],
       [ 0, -1, -1,  0],
       [ 0,  1, -1,  0],
       [ 0,  0,  0,  0]])

In [61]:
optimum_V[(0, 0, -1, 0, 0, -1, -1, 0, 0, 1, -1, 0, 0, 0, 0, 0)]

1

In [62]:
np.array((0, 0, -1, 0, 0, -1, -1, 0, 0, 1, -1, 0, 0, 0, 0, 0)).reshape(4, 4)

array([[ 0,  0, -1,  0],
       [ 0, -1, -1,  0],
       [ 0,  1, -1,  0],
       [ 0,  0,  0,  0]])

# Value Iteration

In [63]:
from dynamic_programming import value_iteration

In [64]:
%%time
V, delta = value_iteration(states, verbose=1)

1 16 2.148329015302604
2 14 1.3984082309742596
3 14 0.7103688654451921
4 13 0.3661814318465639
5 12 0.1380402974781458
6 11 0.05770628692848223
7 10 0.02005554416506682
8 8 0.006710033363777003
9 6 0.0023857896404540454
10 6 0.0005964474101135114
11 6 0.00011183388939628339
12 0 0.0
CPU times: user 6.09 s, sys: 0 ns, total: 6.09 s
Wall time: 6.08 s
